In [1]:
import geopandas as gpd
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import hydrant.topology.geom as gm
import subprocess
import os
from   shapely.geometry import Point
import yaml
import shutil
import warnings
import networkx as nx
import re
import copy


warnings.filterwarnings("ignore")

from riverlakenetwork import BurnLakes


ERROR:tornado.general:Uncaught exception in ZMQStream callback
Traceback (most recent call last):
  File "/Users/shg096/Desktop/RiverLakeNetwork/env/RiverLakeEnv/lib/python3.9/site-packages/traitlets/traitlets.py", line 632, in get
    value = obj._trait_values[self.name]
KeyError: '_control_lock'

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/Users/shg096/Desktop/RiverLakeNetwork/env/RiverLakeEnv/lib/python3.9/site-packages/zmq/eventloop/zmqstream.py", line 565, in _log_error
    f.result()
  File "/Users/shg096/Desktop/RiverLakeNetwork/env/RiverLakeEnv/lib/python3.9/site-packages/ipykernel/kernelbase.py", line 301, in dispatch_control
    async with self._control_lock:
  File "/Users/shg096/Desktop/RiverLakeNetwork/env/RiverLakeEnv/lib/python3.9/site-packages/traitlets/traitlets.py", line 687, in __get__
    return t.cast(G, self.get(obj, cls))  # the G should encode the Optional
  File "/Users/shg096/Desktop/RiverLak

In [2]:
from riverlakenetwork import Utility


In [3]:
# Load general configurations from a YAML file
yaml_file = os.path.abspath('../code/HydroLakes_MERITBasins/HydroLakes_MERITBasins_Config.yaml')
with open(yaml_file, 'r') as f:
    GeneralConfig = yaml.safe_load(f)

# get the path to the merit-basins files
path_out             = GeneralConfig['DomainFolder']
TempFolder           = GeneralConfig['TempFolder']
pfafs                = GeneralConfig['pfafs']
lake_file            = GeneralConfig['LakeFile']
IncludeLakes         = GeneralConfig['IncludeLakes']
riv_path             = GeneralConfig['MERITBasinsPaths']['RivPath']
cat_path             = GeneralConfig['MERITBasinsPaths']['CatPath']
cst_path             = GeneralConfig['MERITBasinsPaths']['CstPath']
riv_file_template    = GeneralConfig['MERITBasinsPaths']['RivFileTemplate']
cat_file_template    = GeneralConfig['MERITBasinsPaths']['CatFileTemplate']
cst_file_template    = GeneralConfig['MERITBasinsPaths']['CstFileTemplate']

In [4]:
if IncludeLakes:
    #load hydrolakeDataset
    lakeO = gpd.read_file(lake_file) # read the hydrolake dataset
    #lakeO = lakeO.loc[lakeO["Hylak_id"] < 200].reset_index(drop=True)
    #lakeO = lakeO.sample(frac=0.10, random_state=42)
    #lakeO = gpd.read_file('lake.gpkg')
    #lakeO = FixHydroLakesForMerit(lakeO) # correct for hydrolakes for merit

# loop over the config files:
for pfaf in ['72']:

    # get the list of pfaf for the subdomain
    subdomain = 'pfaf'+pfaf
    
    # create the folder and domain to include
    path_out_temp = TempFolder+'pfaffff'+pfaf+'/'+subdomain+'/'
    if os.path.isdir(path_out_temp):
        try:
            shutil.rmtree(path_out_temp)  # Remove the entire directory and its contents
        except OSError as e:
            print(f"Error: {path_out_temp} - {e}")
    if not os.path.isdir(path_out_temp):
        os.makedirs(path_out_temp)

    riv, cat = Utility.merit_read_file(pfaf,
                                   riv_file_template='/Users/shg096/Desktop/MERIT_Hydro/riv/riv_pfaf_*_MERIT_Hydro_v07_Basins_v01_bugfix1.shp',
                                   cat_file_template='/Users/shg096/Desktop/MERIT_Hydro/cat/cat_pfaf_*_MERIT_Hydro_v07_Basins_v01_bugfix1.shp',
                                   cst_file_template='/Users/shg096/Desktop/MERIT_Hydro/hill/hillslope_*_clean.shp')

In [5]:
# use DataLoader to
# Example config dictionary
config = {
    "riv": riv,
    "riv_dict": {
        "COMID": {"col":"COMID"},
        "NextDownCOMID": {"col":"NextDownID"},
        "length": {"col":"lengthkm"},
        "uparea": {"col":"uparea","unit":"km2"}
    },
    "cat": cat,
    "cat_dict": {
        "COMID": {"col":"COMID"},
        "unitarea": {"col":"unitarea","unit":"km2"},
    },
    "lake": lakeO,
    "lake_dict": {
        "LakeCOMID": {"col":"Hylak_id"},
        "unitarea": {"col":"Lake_area","unit":"km2"}
    },
}

bl = BurnLakes(config)


=== Input loader started at : 2025-12-17 23:23:05  ===
riv: Loaded
riv_dict: {'COMID': {'col': 'COMID'}, 'NextDownCOMID': {'col': 'NextDownID'}, 'length': {'col': 'lengthkm'}, 'uparea': {'col': 'uparea', 'unit': 'km2'}}
cat: Loaded
cat_dict: {'COMID': {'col': 'COMID'}, 'unitarea': {'col': 'unitarea', 'unit': 'km2'}}
lake: Loaded
lake_dict: {'LakeCOMID': {'col': 'Hylak_id'}, 'unitarea': {'col': 'Lake_area', 'unit': 'km2'}}
=== Input loader finished at: 2025-12-17 23:23:05  ===
=== Input loader took      : 0:00:00.018663  ===========================
=== Input checker started at : 2025-12-17 23:23:05  ===
Subbasin and lake area units are consistent: km2
riv CRS: EPSG:4326
cat CRS: EPSG:4326
lake CRS: EPSG:4326
=== Input checker finished at: 2025-12-17 23:23:05  ===
=== Input checker took      : 0:00:00.083686  ===========================
=== Resolving lakes started at : 2025-12-17 23:23:05  ===
==== Number of lakes after subsetting: 20 ====
==== Number of lakes after removing intersection

In [6]:
bl.cat.to_file("/Users/shg096/Desktop/LakeRiverOut/Tempdomain/pfaffff71/cat1.gpkg")
bl.riv.to_file("/Users/shg096/Desktop/LakeRiverOut/Tempdomain/pfaffff71/riv1.gpkg")
bl.lake.to_file("/Users/shg096/Desktop/LakeRiverOut/Tempdomain/pfaffff71/lake1.gpkg")

In [15]:
print(bl.riv[bl.riv["COMID"] == 72049332])

          COMID  NextDownCOMID  length    uparea geometry  LakeCOMID  \
48556  72049332       72080899     0.0  5.901093     None        NaN   

       unitarea  exorheic  endorheic  islake  ...  up841  up842  up843  up844  \
48556  5.901093       NaN        NaN     NaN  ...      0      0      0      0   

       up845  up846  up847  up848  up849  up850  
48556      0      0      0      0      0      0  

[1 rows x 864 columns]


In [8]:
lakeO

Hylak_id    Lake_name                   Country      Continent Poly_src  \
0           1  Caspian Sea                    Russia         Europe     SWBD   
1           2   Great Bear                    Canada  North America   CanVec   
2           3  Great Slave                    Canada  North America   CanVec   
3           4     Winnipeg                    Canada  North America   CanVec   
4           5     Superior  United States of America  North America     SWBD   
..        ...          ...                       ...            ...      ...   
194       195         None                    Canada  North America   CanVec   
195       196         None                    Canada  North America   CanVec   
196       197    Neergaure                    Canada  North America   CanVec   
197       198         None                    Canada  North America   CanVec   
198       199     Washburn                    Canada  North America   CanVec   

     Lake_type  Grand_id  Lake_area  Shore_len  Shore_dev  ...  Vol_src  \
0            1         0  377001.91   15829.37       7.27  ...        1   
1            1         0   30450.64    5331.72       8.62  ...        1   
2            1         0   26734.29    9814.16      16.93  ...        1   
3            3       709   23923.04    4018.32       7.33  ...        1   
4            1         0   81843.92    5248.36       5.18  ...        1   
..         ...       ...        ...        ...        ...  ...      ...   
194          1         0     126.24     142.30       3.57  ...        3   
195          1         0     327.01     387.54       6.05  ...        3   
196          1         0     166.37     353.51       7.73  ...        3   
197          1         0     103.06     129.80       3.61  ...        3   
198          1         0     255.30     271.42       4.79  ...        3   

     Depth_avg   Dis_avg  Res_time  Elevation  Slope_100  Wshd_area  \
0        200.5  8110.642  107883.0        -29      -1.00  1404108.0   
1         72.2   535.187   47577.7        145      -1.00   147665.4   
2         59.1  4350.692    4203.2        148      -1.00   995312.3   
3         11.9  2244.727    1464.3        215      -1.00   919611.5   
4        146.7  2869.953   48410.3        179      -1.00   209219.5   
..         ...       ...       ...        ...        ...        ...   
194      135.4    12.512   15813.0         26      17.76     1393.6   
195       46.4    12.773   13757.3        538       5.60     1573.7   
196        5.8     7.165    1563.6         14       1.07      920.4   
197       19.7     0.891   26392.2         97       3.47      263.9   
198       27.8     9.886    8303.1         67       3.79     2821.8   

      Pour_long   Pour_lat                                           geometry  
0     47.717708  45.591934  POLYGON ((49.96181 37.43847, 49.96457 37.44022...  
1   -123.505546  65.138384  POLYGON ((-119.78782 67.03574, -119.78637 67.0...  
2   -117.617115  61.311727  POLYGON ((-109.93976 62.95851, -109.93831 62.9...  
3    -97.863542  53.696359  POLYGON ((-98.80636 53.88021, -98.80578 53.880...  
4    -84.460547  46.468593  POLYGON ((-90.7225 46.6574, -90.72458 46.65783...  
..          ...        ...                                                ...  
194  -69.682132  70.485899  POLYGON ((-69.60114 70.52273, -69.59384 70.521...  
195  -73.436694  70.467416  POLYGON ((-73.06774 70.80526, -73.06053 70.804...  
196  -79.684615  70.266809  POLYGON ((-79.95993 70.31561, -79.9592 70.3155...  
197 -106.492381  70.256250  POLYGON ((-106.5563 70.36015, -106.55519 70.36...  
198 -107.176042  70.011628  POLYGON ((-107.61392 70.1531, -107.61113 70.15...  

[199 rows x 22 columns]

In [9]:
len([72080897, 72080899])

2

In [10]:
riv

COMID  lengthkm  lengthdir  sinuosity     slope      uparea order  \
0      72000001  4.861067   3.861534   1.258844  0.014094  133.939982     2   
1      72000002  2.572272   2.348346   1.095355  0.075347   44.704273     1   
2      72000003  1.400671   1.303608   1.074457  0.234509   27.418033     1   
3      72000004  1.914408   1.621514   1.180630  0.004531  664.592208     3   
4      72000005  2.905802   2.048938   1.418199  0.000618  624.169746     3   
...         ...       ...        ...        ...       ...         ...   ...   
80877  72080878  0.000000        NaN        NaN       NaN    0.065442   NaN   
80878  72080879  0.000000        NaN        NaN       NaN    0.095558   NaN   
80879  72080880  0.000000        NaN        NaN       NaN    0.005029   NaN   
80880  72080881  0.000000        NaN        NaN       NaN    0.010058   NaN   
80881  72080882  0.000000        NaN        NaN       NaN    0.030333   NaN   

       strmDrop_t  slope_taud  NextDownID  maxup       up1       up2  up3  \
0            68.7    0.014094       -9999      2  72000030  72000743    0   
1           194.3    0.075347       -9999      0         0         0    0   
2           329.3    0.234509       -9999      0         0         0    0   
3             8.7    0.004531       -9999      2  72000005  72000400    0   
4             1.8    0.000618    72000004      2  72000006  72000264    0   
...           ...         ...         ...    ...       ...       ...  ...   
80877         NaN         NaN       -9999      0         0         0    0   
80878         NaN         NaN       -9999      0         0         0    0   
80879         NaN         NaN       -9999      0         0         0    0   
80880         NaN         NaN       -9999      0         0         0    0   
80881         NaN         NaN       -9999      0         0         0    0   

       up4                                           geometry  
0        0  LINESTRING (-77.38833 62.5225, -77.3875 62.521...  
1        0  LINESTRING (-77.57833 62.51167, -77.5775 62.51...  
2        0  LINESTRING (-77.15417 62.5075, -77.15333 62.50...  
3        0  LINESTRING (-77.61417 61.39667, -77.61333 61.3...  
4        0  LINESTRING (-77.58917 61.405, -77.58833 61.404...  
...    ...                                                ...  
80877    0                                               None  
80878    0                                               None  
80879    0                                               None  
80880    0                                               None  
80881    0                                               None  

[80882 rows x 16 columns]

In [11]:
# 2. Check if riv['COMID'] contains only integers
# Approach 1: check dtype
if pd.api.types.is_integer_dtype(riv["NextDownID"]):
    print("riv['NextDownID'] is integer dtype")
else:
    print("riv['NextDownID'] is NOT integer dtype")

# Approach 2: check all values are integers
if riv["NextDownID"].dropna().apply(lambda x: isinstance(x, int)).all():
    print("All riv['NextDownID'] values are integers")
else:
    print("Not all riv['NextDownID'] values are integers")

riv['NextDownID'] is integer dtype
All riv['NextDownID'] values are integers


In [12]:
riv

COMID  lengthkm  lengthdir  sinuosity     slope      uparea order  \
0      72000001  4.861067   3.861534   1.258844  0.014094  133.939982     2   
1      72000002  2.572272   2.348346   1.095355  0.075347   44.704273     1   
2      72000003  1.400671   1.303608   1.074457  0.234509   27.418033     1   
3      72000004  1.914408   1.621514   1.180630  0.004531  664.592208     3   
4      72000005  2.905802   2.048938   1.418199  0.000618  624.169746     3   
...         ...       ...        ...        ...       ...         ...   ...   
80877  72080878  0.000000        NaN        NaN       NaN    0.065442   NaN   
80878  72080879  0.000000        NaN        NaN       NaN    0.095558   NaN   
80879  72080880  0.000000        NaN        NaN       NaN    0.005029   NaN   
80880  72080881  0.000000        NaN        NaN       NaN    0.010058   NaN   
80881  72080882  0.000000        NaN        NaN       NaN    0.030333   NaN   

       strmDrop_t  slope_taud  NextDownID  maxup       up1       up2  up3  \
0            68.7    0.014094       -9999      2  72000030  72000743    0   
1           194.3    0.075347       -9999      0         0         0    0   
2           329.3    0.234509       -9999      0         0         0    0   
3             8.7    0.004531       -9999      2  72000005  72000400    0   
4             1.8    0.000618    72000004      2  72000006  72000264    0   
...           ...         ...         ...    ...       ...       ...  ...   
80877         NaN         NaN       -9999      0         0         0    0   
80878         NaN         NaN       -9999      0         0         0    0   
80879         NaN         NaN       -9999      0         0         0    0   
80880         NaN         NaN       -9999      0         0         0    0   
80881         NaN         NaN       -9999      0         0         0    0   

       up4                                           geometry  
0        0  LINESTRING (-77.38833 62.5225, -77.3875 62.521...  
1        0  LINESTRING (-77.57833 62.51167, -77.5775 62.51...  
2        0  LINESTRING (-77.15417 62.5075, -77.15333 62.50...  
3        0  LINESTRING (-77.61417 61.39667, -77.61333 61.3...  
4        0  LINESTRING (-77.58917 61.405, -77.58833 61.404...  
...    ...                                                ...  
80877    0                                               None  
80878    0                                               None  
80879    0                                               None  
80880    0                                               None  
80881    0                                               None  

[80882 rows x 16 columns]